In [14]:
###########import packages##########
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import matplotlib.pyplot as plt
import tensorflow as tf 
from sklearn.model_selection import GridSearchCV
import xgboost as xgb
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import LabelBinarizer
%matplotlib
###########assign memory##########
###########delete this part if your tensorflow was based on CPU##########
# config = tf.ConfigProto()
# config.gpu_options.allocator_type = 'BFC' #A "Best-fit with coalescing" algorithm, simplified from a version of dlmalloc.
# config.gpu_options.per_process_gpu_memory_fraction = 0.5
# config.gpu_options.allow_growth = True
# set_session(tf.Session(config=config)) 
###########fix random seed for reproducability##########
seed=1
np.random.seed(seed)
###########wrapping root mean square error for later calls##########
def rmse(predictions, targets):
    return np.sqrt(((predictions - targets) ** 2).mean())
###########loading data##########
fdata=pd.read_csv('0721platinum.csv',encoding="gbk")
raw_data=fdata.loc[:,[                     
                      'Pt at% in metal element',#0
                      'Pd at% in metal element',#1
                      'Au at% in metal element',#2
                      'Ir at% in metal element',#3
                      'Ru at% in metal element',#4
                      'Ni at% in metal element',#5
                      'Co at% in metal element',#6
                      'Fe at% in metal element',#7
                      'Cu at% in metal element',#8
                      'Cr at% in metal element',#9
                      'Mo at% in metal element',#10
                      'Sc at% in metal element',#11
                      'total metal mass ratio wt%',#12
                      'N at%',#13
                      'S at%',#14
                      'O at%',#15
                      'Ti at%',#16
                      'C wt%',#17
                      'Particle diameter （nm）',#18
                      'support BET surface area(m2/g)' ,#19
                      'particle',#20 
                      'nanowire',#21
                      'core-shell',#22
                      'Reduction Temperature',#23
                      'Reduction Time/min',#24
                      'mircrowave(0/1)',#25   
                      'polyhydric alcohols',#26
                      'heat reduction',#27
                      'inorganic reducing agent',#28
                      'organic reducing agent',#29
                      'pH',#30
                      'Annealing Temperature',#31
                      'Annealing Time/h',#32
                      'Atomosphere h2',#33
                      'Atomosphere inert',#34
                      'ECSA m2/g',#35
                      'Mass Activity mA mg-1',#36
                      'Specific Activity mA cm-2',#37   
                      'I/C Ratio(ionomer/catalyst)',#38
                      'Area cm2',#39
                      'Cathodic Loading Amount mgPt cm-2',#40
                      'Anodic Platinum Loading Amount mgPt cm-2',#41
                      'Anodic catalyst type x wt% Pt/C',#42
                      'membrane thickness',#43
                      'Hot Press Temperature',#44
                      'Hot Press Time min',#45
                      'Hot Press Pressure Mpa',#46
                      'Humidity %',#47
                      'GDE for 1',#48
                      'celltemp',#49
                      'Flowing rate of H2 ml min-1',#50
                      'flowing rate of cathode gas(O2/air)',#51
                      'Back Pressure Mpa',#52
                      'Cathode gas oxygen ratio',#53
                      'Maximum Power Density mW cm-2'#
                        ]]
###########handling missing values##########
median_raw_data=raw_data.median()
dict_median_raw_data=median_raw_data.to_dict()
data=raw_data.fillna(dict_median_raw_data)
###########data standardization##########
standardized_data = (data-np.mean(data,axis=0))/np.std(data,axis=0)
###########train test splitting##########
raw_param=standardized_data.iloc[:,0:54]
raw_power=standardized_data.iloc[:,54]
X=raw_param.values.astype(np.float32)
y=raw_power.values.astype(np.float32)
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=.15, random_state=seed)
###########defining a wrapper function for later call from each machine learning algorithms##########
def try_different_method(model):
    model.fit(X_train,y_train)
    score = model.score(X_test, y_test)
    result = model.predict(X_test)
    x_prediction_maximum_power_ann=result*np.std(data,axis=0)[53]+np.mean(data,axis=0)[53]
    y_real_maximum_power=y_test*np.std(data,axis=0)[53]+np.mean(data,axis=0)[53]
    print(x_prediction_maximum_power_ann)
    x_prediction_maximum_power_ann_series=pd.Series(x_prediction_maximum_power_ann)
    y_real_maximum_power_series=pd.Series(y_real_maximum_power)
    ###########evaluating the regression quality##########
    corr_ann = round(x_prediction_maximum_power_ann_series.corr(y_real_maximum_power_series), 4)
    rmse_val= rmse(x_prediction_maximum_power_ann,y_real_maximum_power)
    print(rmse_val)
    print(corr_ann)
    print(y_real_maximum_power)
    ###########generating a figure##########
    x_y_x=np.arange(0,3000,100)
    x_y_y=np.arange(0,3000,100)
    fig = plt.figure()
    ax = fig.add_subplot(111)
    ax.scatter(x_prediction_maximum_power_ann,y_real_maximum_power,color='red',label=algorithm_name)
    ax.plot(x_y_x,x_y_y)
    plt.legend()
    plt.xlabel(u"Predicted_Maximum_Power mw cm^-2")
    plt.ylabel(u"Real_Maximum_Power mw cm^-2")
    plt.show()
####import machine learning algorithms packages and define the corresponding models####
####Decision Tree####
from sklearn import tree
from sklearn.tree import DecisionTreeRegressor
from sklearn import metrics
model_DecisionTreeRegressor = tree.DecisionTreeRegressor()
####Linear Regression####
from sklearn import linear_model
model_LinearRegression = linear_model.LinearRegression()
####Support Vector Regressor####
from sklearn import svm
model_SVR = svm.SVR()
####K Nearest Neighbor####
from sklearn import neighbors
model_KNeighborsRegressor = neighbors.KNeighborsRegressor()
####Random Forest####
from sklearn import ensemble
model_RandomForestRegressor = ensemble.RandomForestRegressor()
####Adaboost####
from sklearn import ensemble
model_AdaBoostRegressor = ensemble.AdaBoostRegressor()
####GBRT####
from sklearn import ensemble
model_GradientBoostingRegressor = ensemble.GradientBoostingRegressor()
####Bagging Regressor ####
from sklearn.ensemble import BaggingRegressor
model_BaggingRegressor = BaggingRegressor()
####Extra Tree Regressor####
from sklearn.tree import ExtraTreeRegressor
model_ExtraTreeRegressor = ExtraTreeRegressor()
####Bayesian Ridge####
from sklearn.linear_model import BayesianRidge
model_BayesianRidge =BayesianRidge()
####Gaussian Process####
from sklearn.gaussian_process import GaussianProcessRegressor
model_GaussianProcessRegressor=GaussianProcessRegressor()
####SGD####
from sklearn.linear_model.stochastic_gradient import SGDRegressor
model_SGDRegressor=SGDRegressor()
####Ridge Regressor####
from sklearn.linear_model import Ridge,RidgeCV
model_RidgeRegressor=Ridge()
####Kernel Ridge####
from sklearn.kernel_ridge import KernelRidge
model_KernelRidgeRegressor=KernelRidge()
####XGBoost####
import xgboost as xgb
model_XGboostRegressor=xgb.XGBRegressor()

####CatBoost####
import catboost
model_CatboostRegressor=catboost.CatBoostRegressor()
####LightGBM####
import lightgbm
model_LGBMRegressor=lightgbm.LGBMRegressor()








####Lasso Regressor####
from sklearn import linear_model
model_LassoRegressor=linear_model.Lasso()
####Elastic Net####
from sklearn import linear_model
model_ElasticNetRegressor=linear_model.ElasticNet()
####Elastic NetCV####
from sklearn import linear_model
model_ElasticNetCVRegressor=linear_model.ElasticNetCV()
####LARS####
from sklearn import linear_model
model_LARSRegressor=linear_model.Lars()
####LARSCV####
from sklearn import linear_model
model_LARSCVRegressor=linear_model.LarsCV()
####OMP####
from sklearn import linear_model
model_OMPRegressor=linear_model.OrthogonalMatchingPursuit()
####OMPCV####
from sklearn import linear_model
model_OMPCVRegressor=linear_model.OrthogonalMatchingPursuitCV()
####ARD####
from sklearn import linear_model
model_ARDRegressor=linear_model.ARDRegression()
####PAR####
from sklearn import linear_model
model_PARRegressor=linear_model.PassiveAggressiveRegressor()
####RANSAC####
from sklearn import linear_model
model_RANSACRegressor=linear_model.RANSACRegressor()
####TSR####
from sklearn import linear_model
model_TSRRegressor=linear_model.TheilSenRegressor()
####Huber####
from sklearn import linear_model
model_HuberRegressor=linear_model.HuberRegressor()
####Polynomial####
from sklearn import linear_model
from sklearn.linear_model import LinearRegression
from sklearn.preprocessing import PolynomialFeatures
from sklearn.pipeline import Pipeline
model_PolynomialRegressor=Pipeline([('poly', PolynomialFeatures(degree=4)),('linear', LinearRegression(fit_intercept=False))])
####Linear Support Vector Regressor####
from sklearn import svm
model_LinearSVR = svm.LinearSVR()
####Nu Support Vector Regressor####
from sklearn import svm
model_NuSVR = svm.NuSVR()
####Radius Nearest Neighbor####
from sklearn import neighbors
model_RadiusNeighborsRegressor = neighbors.RadiusNeighborsRegressor()
####Voting Regressor ####
from sklearn.ensemble import VotingRegressor
model_VotingRegressor = VotingRegressor(5)
####Stacking Regressor ####
from sklearn.ensemble import StackingRegressor
model_StackingRegressor = StackingRegressor(5)


Using matplotlib backend: Qt5Agg


In [13]:
seed=2
np.random.seed(seed)
####Decision Tree####
###########defining the parameters dictionary##########
# param = {'criterion':['mse','mae','friedman_mse'],
#          'max_depth':range(5,15),
#          'splitter':['random','best'],
#          'min_samples_split':range(2,10),
#          'max_features':["auto", "sqrt", "log2"]
#        }
param = {
         'max_features':["auto", "sqrt", "log2"]
       }
grid = GridSearchCV(model_DecisionTreeRegressor,param_grid=param,cv=5)
grid.fit(X_train,y_train)
print('Best Regressor:',grid.best_params_,'Best Score:', grid.best_score_) 
best_model=grid.best_estimator_

algorithm_name='Decision Tree Regressor'
try_different_method(best_model)

Best Regressor: {'max_features': 'auto'} Best Score: 0.40995812913888263
[1814.99997907  467.99999717  527.99999971  949.19999586 1240.40999915
 1271.48999943  311.49999609 1385.99998185 1814.99997907  280.00000645
  252.00001018  459.0000054   147.99000791  421.57499708  363.99999524
 1091.5449875   400.00001152  245.85400015  200.00000306  151.99998135
  160.00000137  949.19999586  343.99999439  531.27800539  252.00001018
 1091.5449875  1240.16999117 1008.00000769  437.82399989  494.99999708
  604.99999866  360.00000983 2321.73003949  739.49999696  369.99999795
  588.00000224  911.99998888 1475.64001058 1893.93003297  445.49999929
 1121.4600167   660.00000021 1271.28000475 1196.00001072  400.00001152
  409.99999964  818.99999602 1043.48999472  252.00001018  201.60000707
 1729.5299783  1103.42999526 1046.40000538 1351.99998287  576.00000297
  363.99999524  355.50000779  329.51700357   36.99999494  346.50000372
  252.00001018  252.00001018 1042.4999987   450.00000133  332.50000559
 112

In [6]:
seed=2
np.random.seed(seed)
####Support Vector Regressor####
###########defining the parameters dictionary##########
param = {'kernel':['rbf','linear','poly'],'max_iter':[100,200,300,400,500,600,700,800,1000,1100,1200,1300,1400,1500],
         'degree':[2,3,4],
         'gamma':['scale','auto'],
         'epsilon':[0.001,0.01,0.1,0.3,0.5,0.7,1],'coef0':[100,200,300,400,500,600,700,800,1000,1100,1200,1300,1400,1500]
       }
grid = GridSearchCV(model_SVR,param_grid=param,cv=5)
grid.fit(X_train,y_train)
print('Best Regressor:',grid.best_params_,'Best Score:', grid.best_score_) 
best_model=grid.best_estimator_

algorithm_name='Support Vector Regressor'
try_different_method(best_model)

D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminate

D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=500).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=500).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=500).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=500).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminate

D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=1300).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=1300).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=1400).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=1400).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver termi

D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=600).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=600).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=700).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=700).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminate

D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=200).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=200).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=200).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=200).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminate

...

D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=1100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=1100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=1100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=1200).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver termi

D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=800).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=800).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=800).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=800).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminate

D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminate

D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=1100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=1100).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=1200).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver terminated early (max_iter=1200).  Consider pre-processing your data with StandardScaler or MinMaxScaler.
  % self.max_iter, ConvergenceWarning)
D:\anaconda\lib\site-packages\sklearn\svm\_base.py:231: ConvergenceWarning: Solver termi

KeyboardInterrupt: 

In [12]:
seed=2
np.random.seed(seed)
####K Nearest Neighbor####
###########defining the parameters dictionary##########
param = {'n_neighbors':range(1,10),'weights':['uniform','distance'],'algorithm':['auto', 'ball_tree', 'kd_tree', 'brute'],
         'leaf_size':[2,10,20,30,40,50,100],
         'p':range(1,10)
       }
grid = GridSearchCV(model_KNeighborsRegressor,param_grid=param,cv=5)
grid.fit(X_train,y_train)
print('Best Regressor:',grid.best_params_,'Best Score:', grid.best_score_) 
best_model=grid.best_estimator_

algorithm_name='KNeighbors Regressor'
try_different_method(best_model)

Best Regressor: {'algorithm': 'brute', 'leaf_size': 2, 'n_neighbors': 9, 'p': 1, 'weights': 'distance'} Best Score: 0.32113639285877216
[647.56277655 384.69404652 503.16268424 807.56730289 848.57025049
 665.59557274 496.01863951 681.4592564  491.92028834 533.81439024
 824.08971187 436.22579663 644.89632863 573.21027067 483.33091053
 423.49753939 514.92746911 702.25296914 786.33853742 385.04108061
 640.61482767]
112.0487988187753
0.8718
[750.  292.5 450.  940.  810.  680.  700.  450.  430.  365.  850.  300.
 650.  506.  360.  320.  530.  870.  810.  320.  530. ]


In [13]:
seed=2
np.random.seed(seed)
####Random Forest####
###########defining the parameters dictionary##########
param = {'n_estimators':[200,400,800],
         'max_depth':[5,10,15],
         'min_samples_split':[2,4,6,8],
         'min_samples_leaf':[2,4,8],
         'max_features':['auto','sqrt','log2']

       }

grid = GridSearchCV(model_RandomForestRegressor,param_grid=param,cv=5)
grid.fit(X_train,y_train)
print('Best Regressor:',grid.best_params_,'Best Score:', grid.best_score_) 
best_model=grid.best_estimator_

algorithm_name='Random Forest Regressor'
try_different_method(best_model)

Best Regressor: {'max_depth': 15, 'max_features': 'log2', 'min_samples_leaf': 2, 'min_samples_split': 4, 'n_estimators': 200} Best Score: 0.4332118606318078
[651.00046334 445.3948151  534.12270367 728.24035696 912.08108177
 628.11393823 453.00145672 647.76778356 495.9490735  503.10260167
 765.9310046  400.91510094 642.69750002 524.35390368 421.33135353
 457.92660907 554.21561946 701.11725395 768.35164899 479.56991734
 624.5200294 ]
124.86508769417117
0.8265
[750.  292.5 450.  940.  810.  680.  700.  450.  430.  365.  850.  300.
 650.  506.  360.  320.  530.  870.  810.  320.  530. ]


In [14]:
seed=2
np.random.seed(seed)
####Gradient Boost####
###########defining the parameters dictionary##########
param = {'n_estimators':[200,400,800],
         'max_depth':[5,10,15],
         'min_samples_split':[2,4,6,8],
         'max_features':['auto','sqrt','log2'],
         'loss':['ls', 'lad', 'huber', 'quantile'],
         'learning_rate':[0.01,0.1,0.2],
         'criterion':['friedman_mse'],
         'subsample':[0.6,0.8,1]
       }
grid = GridSearchCV(model_GradientBoostingRegressor,param_grid=param,cv=5)
grid.fit(X_train,y_train)
print('Best Regressor:',grid.best_params_,'Best Score:', grid.best_score_) 
best_model=grid.best_estimator_

algorithm_name='Gradient Boost Regressor'
try_different_method(best_model)

Best Regressor: {'criterion': 'friedman_mse', 'learning_rate': 0.1, 'loss': 'huber', 'max_depth': 5, 'max_features': 'log2', 'min_samples_split': 2, 'n_estimators': 400, 'subsample': 0.6} Best Score: 0.46828979669946935
[ 690.6755479   385.27565812  528.44870334 1011.5818276   883.2545369
  692.53369456  534.45073406  695.14672397  468.37391389  459.63591541
  958.90075438  390.53814697  725.3030851   462.23162092  364.90365148
  480.931399    561.77026994  771.24281334  836.41516878  301.72963659
  647.47219162]
99.04773084153223
0.9059
[750.  292.5 450.  940.  810.  680.  700.  450.  430.  365.  850.  300.
 650.  506.  360.  320.  530.  870.  810.  320.  530. ]


In [16]:
seed=2
np.random.seed(seed)
####SGD####
###########defining the parameters dictionary##########
param = {'loss':['squared_loss', 'huber','epsilon_insensitive','squared_epsilon_insensitive'],
         'penalty':['l2', 'elasticnet'],
         'fit_intercept':[True,False],
         'max_iter':[500,1000,2000],
         'epsilon':[0.001,0.01,0.1,1],
         'learning_rate':['invscaling','constant', 'optimal', 'adaptive']
       }
grid = GridSearchCV(model_SGDRegressor,param_grid=param,cv=5)
grid.fit(X_train,y_train)
print('Best Regressor:',grid.best_params_,'Best Score:', grid.best_score_) 
best_model=grid.best_estimator_

algorithm_name='Stochastic Gradient Descent Regressor'
try_different_method(best_model)

Best Regressor: {'epsilon': 1, 'fit_intercept': False, 'learning_rate': 'invscaling', 'loss': 'epsilon_insensitive', 'max_iter': 2000, 'penalty': 'elasticnet'} Best Score: 0.2627201532798342
[583.05688682 561.25005701 412.57398699 595.9951642  809.69455208
 672.13674362 464.03753735 430.37463849 587.45929276 525.89072511
 769.10024032 552.70723836 606.83344721 317.47666933 510.50838943
 525.92513715 569.01188205 717.03077965 716.03042757 458.87520174
 689.71092962]
165.9109045986851
0.6025
[750.  292.5 450.  940.  810.  680.  700.  450.  430.  365.  850.  300.
 650.  506.  360.  320.  530.  870.  810.  320.  530. ]


In [4]:
seed=2
np.random.seed(seed)
####Bagging Regressor####
###########defining the parameters dictionary##########
param = {'n_estimators':[10,50,100,200,400],
         'max_samples':[5,10,50,100],
         'max_features':[5,10,25]
       }
grid = GridSearchCV(model_BaggingRegressor,param_grid=param,cv=5)
grid.fit(X_train,y_train)
print('Best Regressor:',grid.best_params_,'Best Score:', grid.best_score_) 
best_model=grid.best_estimator_

algorithm_name='Bagging Regressor'
try_different_method(best_model)

D:\anaconda\lib\site-packages\sklearn\model_selection\_validation.py:536: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
ValueError: max_samples must be in (0, n_samples]

  FitFailedWarning)
D:\anaconda\lib\site-packages\sklearn\model_selection\_validation.py:536: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
ValueError: max_samples must be in (0, n_samples]

  FitFailedWarning)
D:\anaconda\lib\site-packages\sklearn\model_selection\_validation.py:536: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
ValueError: max_samples must be in (0, n_samples]

  FitFailedWarning)
D:\anaconda\lib\site-packages\sklearn\model_selection\_validation.py:536: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters w

D:\anaconda\lib\site-packages\sklearn\model_selection\_validation.py:536: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
ValueError: max_samples must be in (0, n_samples]

  FitFailedWarning)
D:\anaconda\lib\site-packages\sklearn\model_selection\_validation.py:536: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
ValueError: max_samples must be in (0, n_samples]

  FitFailedWarning)
D:\anaconda\lib\site-packages\sklearn\model_selection\_validation.py:536: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters will be set to nan. Details: 
ValueError: max_samples must be in (0, n_samples]

  FitFailedWarning)
D:\anaconda\lib\site-packages\sklearn\model_selection\_validation.py:536: FitFailedWarning: Estimator fit failed. The score on this train-test partition for these parameters w

Best Regressor: {'max_features': 25, 'max_samples': 50, 'n_estimators': 100} Best Score: 0.4224534528033475
[652.53999868 587.18000289 543.44500151 632.90000188 863.47666411
 698.64999848 485.32999925 638.86499853 486.12500045 505.44000068
 727.26000218 422.39999981 636.11500005 503.23000034 469.76000205
 511.09833441 553.05500041 698.37333243 791.57999571 476.51000021
 655.46166535]
147.45249959704483
0.7444
[750.  292.5 450.  940.  810.  680.  700.  450.  430.  365.  850.  300.
 650.  506.  360.  320.  530.  870.  810.  320.  530. ]


In [22]:
seed=2
np.random.seed(seed)
####extreme tree####
###########defining the parameters dictionary##########
param = {
         'criterion' : ["mse", "friedman_mse", "mae"],
        'splitter' : [ "best",'random'],
       'max_depth':range(5,15),
       'min_samples_split':[2,4,6,8],
         'min_samples_leaf':[1,2,4,8]
       }
grid = GridSearchCV(model_ExtraTreeRegressor,param_grid=param,cv=5)
grid.fit(X_train,y_train)
print('Best Regressor:',grid.best_params_,'Best Score:', grid.best_score_) 
best_model=grid.best_estimator_

algorithm_name='Extra Tree Regressor'
try_different_method(best_model)

Best Regressor: {'criterion': 'mse', 'max_depth': 14, 'min_samples_leaf': 4, 'min_samples_split': 8, 'splitter': 'random'} Best Score: 0.38409510564627386
[677.99999955 491.21428893 428.83333171 491.21428893 950.09999989
 677.99999955 428.83333171 750.749998   428.83333171 428.83333171
 694.60000517 355.39999805 750.749998   507.50000101 411.0000028
 491.21428893 532.14285653 789.7499979  752.49999624 355.39999805
 624.44444371]
157.87702882134198
0.661
[750.  292.5 450.  940.  810.  680.  700.  450.  430.  365.  850.  300.
 650.  506.  360.  320.  530.  870.  810.  320.  530. ]


In [24]:
seed=2
np.random.seed(seed)
####Kernel Ridge####
###########defining the parameters dictionary##########
param = {
         'alpha':[1,1.5,2],
        'kernel':['rbf', 'linear'],
        'gamma':[0.1,0.5,1,2],
        'degree':[2,3,4],
        'coef0':[0.01,0.1,0.5,1,10,50,100,200,500,1000]
         
       }
grid = GridSearchCV(model_KernelRidgeRegressor,param_grid=param,cv=5)
grid.fit(X_train,y_train)
print('Best Regressor:',grid.best_params_,'Best Score:', grid.best_score_) 
best_model=grid.best_estimator_

algorithm_name='Kernel Ridge Regressor'
try_different_method(best_model)

Best Regressor: {'alpha': 1, 'coef0': 0.01, 'degree': 2, 'gamma': 0.1, 'kernel': 'rbf'} Best Score: 0.3727441645648451
[611.74554 480.7367  589.632   729.26025 880.75977 591.61847 512.51715
 689.1711  521.9326  489.4097  731.9265  516.54755 581.8218  565.5569
 522.3319  565.9397  524.7916  702.7681  765.1538  567.36743 631.79944]
155.07019
0.7334
[750.  292.5 450.  940.  810.  680.  700.  450.  430.  365.  850.  300.
 650.  506.  360.  320.  530.  870.  810.  320.  530. ]


In [25]:
seed=2
np.random.seed(seed)
####Ridge Regressor####
###########defining the parameters dictionary##########
param = {
         'alpha':[0.1,0.2,0.4,0.8,1,1.6,2,4,8],
        'solver':['saga','auto']  
       }
grid = GridSearchCV(model_RidgeRegressor,param_grid=param,cv=5)
grid.fit(X_train,y_train)
print('Best Regressor:',grid.best_params_,'Best Score:', grid.best_score_) 
best_model=grid.best_estimator_

algorithm_name='Ridge Regressor'
try_different_method(best_model)

Best Regressor: {'alpha': 8, 'solver': 'saga'} Best Score: -0.05102050969897378
[522.8762  543.4666  440.7545  584.29913 818.3574  658.9734  426.77298
 422.25754 583.4714  499.99756 778.38416 601.5723  691.14246 255.73245
 527.1688  492.81006 584.58405 649.84076 742.70764 322.50177 682.56744]
176.79167
0.5411
[750.  292.5 450.  940.  810.  680.  700.  450.  430.  365.  850.  300.
 650.  506.  360.  320.  530.  870.  810.  320.  530. ]


In [26]:
seed=2
np.random.seed(seed)
####Bayesian Rdige Regressor####
###########defining the parameters dictionary##########
param = {
         'n_iter':[50,100,200,400,800],  
       }
grid = GridSearchCV(model_BayesianRidge,param_grid=param,cv=5)
grid.fit(X_train,y_train)
print('Best Regressor:',grid.best_params_,'Best Score:', grid.best_score_) 
best_model=grid.best_estimator_

algorithm_name='Bayesian Ridge Regressor'
try_different_method(best_model)

Best Regressor: {'n_iter': 50} Best Score: 0.2040537353007509
[553.62098026 553.9406663  479.87943797 569.00601974 782.25497684
 653.41312858 457.01014734 458.23207949 579.35699785 526.62691117
 719.21762941 594.13417016 622.49734937 371.85600461 555.00409469
 562.42526443 567.72987168 627.46936034 721.82636826 401.56043158
 664.04655826]
178.1212654844881
0.5147
[750.  292.5 450.  940.  810.  680.  700.  450.  430.  365.  850.  300.
 650.  506.  360.  320.  530.  870.  810.  320.  530. ]


In [27]:
seed=2
np.random.seed(seed)
####XGboost####
###########defining the parameters dictionary##########
param = {
         'learning_rate':[0.01,0.1,1],
   'n_estimators':[100,200,400,1000,2000,4000,8000],
    'max_depth':[5,7,9,11],
    'objective':['reg:squarederror'],
    'subsample':[0.5,0.6,0.7,0.8,0.9],
    'lambda':[0.1],
    'alpha':[0.1]
       }
grid = GridSearchCV(model_XGboostRegressor,param_grid=param,cv=5)
grid.fit(X_train,y_train)
print('Best Regressor:',grid.best_params_,'Best Score:', grid.best_score_) 
best_model=grid.best_estimator_

algorithm_name='XGBoost Regressor'
try_different_method(best_model)

Best Regressor: {'alpha': 0.1, 'lambda': 0.1, 'learning_rate': 0.01, 'max_depth': 5, 'n_estimators': 400, 'objective': 'reg:squarederror', 'subsample': 0.5} Best Score: 0.41268368118925897
[684.6948  471.60583 497.30203 881.95074 858.19836 706.3307  471.4709
 649.4955  473.2922  477.57037 877.8537  419.58356 669.22766 466.1802
 388.0565  392.06738 555.401   735.57837 789.2324  463.16248 632.19763]
103.42592
0.8873
[750.  292.5 450.  940.  810.  680.  700.  450.  430.  365.  850.  300.
 650.  506.  360.  320.  530.  870.  810.  320.  530. ]


In [5]:
seed=2
np.random.seed(seed)
####Adaboost####
###########defining the parameters dictionary##########
param = {'n_estimators':[300,500,700,1000],
         'learning_rate':[0.01,0.1,1,2],
         'loss':[ 'square']
       }
grid = GridSearchCV(model_AdaBoostRegressor,param_grid=param,cv=5)
grid.fit(X_train,y_train)
best_model=grid.best_estimator_

print('Best Regressor:',grid.best_params_,'Best Score:', grid.best_score_) 
best_model=grid.best_estimator_

algorithm_name='AdaBoost Regressor'
try_different_method(best_model)

Best Regressor: {'learning_rate': 1, 'loss': 'square', 'n_estimators': 700} Best Score: 0.4162746906191234
[686.99999882 397.08196994 453.54285998 908.87500006 919.00000078
 792.66666555 464.91836822 582.55072566 474.17500219 486.73913175
 858.69999806 412.2941206  662.49999975 441.4999998  433.42105535
 398.90909374 441.36986448 820.4268277  725.42499859 431.32258066
 609.03174679]
96.31083615133979
0.8936
[750.  292.5 450.  940.  810.  680.  700.  450.  430.  365.  850.  300.
 650.  506.  360.  320.  530.  870.  810.  320.  530. ]


In [28]:
seed=2
np.random.seed(seed)
####Linear Regressor####

algorithm_name='Linear Regressor'
try_different_method(model_LinearRegression)

[671.3449  524.4938  345.14676 648.5534  852.8313  690.80804 394.91248
 481.4383  618.8418  525.4126  839.53    569.56476 681.96313 153.66754
 383.04706 323.95392 583.3732  662.2241  783.9317  176.51428 638.5851 ]
167.74611
0.6524
[750.  292.5 450.  940.  810.  680.  700.  450.  430.  365.  850.  300.
 650.  506.  360.  320.  530.  870.  810.  320.  530. ]


In [29]:
seed=2
np.random.seed(seed)
####Gaussian Process Regressor####

algorithm_name='Gaussian Process Regressor'
try_different_method(model_GaussianProcessRegressor)

[616.07594608 403.40864049 594.27035313 698.79763404 771.87482351
 593.13954634 559.75269834 675.12607566 479.31963131 491.46572789
 686.85788264 561.3762549  593.27867283 593.26633873 590.06334578
 593.25253566 653.22925216 687.57935809 815.11343439 593.27781679
 606.61983614]
164.66505489587888
0.6948
[750.  292.5 450.  940.  810.  680.  700.  450.  430.  365.  850.  300.
 650.  506.  360.  320.  530.  870.  810.  320.  530. ]


In [22]:
seed=2
np.random.seed(seed)
####Lasso Regressor####
from sklearn import linear_model
param = {
         'max_iter':[50,100,200,400,800,1600],  
       }
grid = GridSearchCV(model_LassoRegressor,param_grid=param,cv=5)
grid.fit(X_train,y_train)
print('Best Regressor:',grid.best_params_,'Best Score:', grid.best_score_) 
best_model=grid.best_estimator_

algorithm_name='Lasso Regressor'
try_different_method(best_model)

Best Regressor: {'max_iter': 50} Best Score: -0.018078202001586476
[654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636

In [19]:
seed=2
np.random.seed(seed)
####Lasso Regressor####
from sklearn import linear_model

algorithm_name='Elastic Net'
try_different_method(model_ElasticNetRegressor)

[654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636 654.45636
 654.4

In [20]:
seed=2
np.random.seed(seed)
####Lasso Regressor####
from sklearn import linear_model

algorithm_name='Elastic NetCV'
try_different_method(model_ElasticNetCVRegressor)

[ 711.25977    802.5992     805.55023    621.1796     469.28894
  562.5839     272.1458     814.8773     663.5091     742.54034
  674.94275    844.5227     543.7981     722.20215    616.10156
  754.6766     476.79514    658.6577     711.25977    677.9332
  618.0629     550.3537     518.9823     768.4811     155.12247
  787.6292     644.4203     117.228516   985.67053    676.23126
  715.575      528.7905     747.95825    590.4933     895.85516
  639.5508     830.3044     540.0761     418.53265    643.00726
  778.06195    233.98444    918.8501     747.7075     705.3744
  519.8153     567.0514     587.03625    530.05505    910.1609
  411.67126    682.53595   1031.5088     479.90515    825.1317
 1765.2778     601.47723    674.17096    234.7013     780.2801
  431.4552     568.33307    767.7734     772.4711     379.72995
  519.8153     601.11334    345.6267     956.354      910.8722
  432.99353    547.98376    669.44415    510.80322    554.2699
  356.7632     590.4076     730.93634    690.51

In [25]:
seed=2
np.random.seed(seed)
####LARS Regressor####
from sklearn import linear_model

algorithm_name='LARS'
try_different_method(model_LARSRegressor)

[ 3.59495604e+03  1.69512477e+04 -1.27126930e+03  1.66402196e+04
  1.16734850e+04  7.36829548e+03 -1.94017597e+04 -5.21814387e+03
 -6.14725266e+03 -1.13425069e+03  9.71847118e+03  5.37045106e+03
 -2.33119225e+06  4.78261732e+03 -1.45450589e+04 -5.35954999e+03
 -1.72341000e+04 -1.57381027e+04  3.59495604e+03 -1.38250766e+04
  1.13698682e+04  1.10853602e+04  3.44515147e+03  6.24595904e+03
 -1.22695968e+04 -1.72527028e+04 -8.31293913e+02  1.85688645e+04
  3.97954504e+04 -2.02836006e+04  6.68788449e+03 -3.04056068e+03
  2.14065885e+04  1.16227199e+04  1.55859673e+04 -3.75042696e+03
 -1.20673856e+04  6.37039698e+02  4.18887482e+03 -2.94488347e+03
 -3.96949803e+03 -9.36328631e+03 -1.27826001e+03 -8.36358642e+02
  2.21581067e+04 -3.47073479e+03 -3.83173042e+03  3.80387811e+03
 -1.79084819e+04 -1.25584297e+04 -2.02220185e+03  1.06301416e+04
  1.05549149e+04 -1.79301665e+04  2.83378389e+03  3.26333312e+04
  2.08034125e+04  1.51907301e+04 -8.98538538e+03 -4.78045310e+03
 -1.39053193e+04 -5.72924

In [26]:
seed=2
np.random.seed(seed)
####LARS Regressor####
from sklearn import linear_model

algorithm_name='LARSCV'
try_different_method(model_LARSCVRegressor)

[ 688.5268258   791.97079474  809.81237492  653.27108695  471.31376134
  543.99511703  285.0942902   806.50442893  650.00878256  749.35043759
  692.42137895  824.7355918   555.70451415  692.82990049  615.39203486
  774.42652902  531.73105146  683.14102418  688.5268258   675.50518463
  601.57550605  557.21654255  519.55660907  777.6477237   204.55903068
  804.30005284  654.2906693   126.14698794  889.0111319   641.64334489
  652.27248266  550.58464728  744.93958703  571.4639645   866.19530826
  694.16069903  825.03137022  517.18312146  381.96649571  651.21046896
  806.55334501  335.92097853  913.5836571   751.21578304  671.43114733
  542.2095747   649.13167804  585.60491256  517.6630103   820.98091207
  426.09890425  692.88764695  968.14982332  534.69862823  792.09951047
 1682.07466809  616.35978101  626.28064212  336.25702174  736.37583678
  454.38151441  569.20926153  721.9166364   745.39078955  397.89118943
  542.2095747   621.11752084  339.53248655  924.03055166  736.55440598
  486.

In [49]:
seed=2
np.random.seed(seed)

####Polynomial####

algorithm_name='Polynomial'
try_different_method(model_PolynomialRegressor)

[ 5.9243604e+02  2.0578303e+03  9.4099365e+02  4.7298447e+02
  2.1106146e+02  9.0135620e+02  1.1964581e+02  8.4651526e+02
  6.5289081e+02  4.1231763e+02  5.6833875e+02  1.0286484e+03
  1.3121094e+01  6.1768604e+02  4.2894901e+02  4.4584177e+02
  5.1380621e+02  1.2089404e+02  5.9243604e+02  4.3817957e+02
  4.8794122e+02  5.4637848e+02  5.3511975e+02 -3.5483872e+05
  2.6968903e+02  3.0794748e+02 -8.0037848e+02  6.8480438e+02
 -9.0224933e+02  2.2139592e+03  5.7929077e+02  3.5484558e+01
  8.5802142e+02  2.3080273e+02  1.0481488e+03  9.6241980e+02
 -5.2184833e+02  9.1921063e+02  7.3351135e+02  3.0313724e+02
  5.2711475e+02  8.6877869e+01  1.8587671e+03  2.8113525e+02
  4.7567667e+02  5.0982294e+02  8.0381262e+02  7.3731287e+02
  1.0971816e+03  9.6572742e+02  1.1130830e+03  6.6571350e+02
  1.7222439e+03  8.9687378e+02  4.6004614e+02  1.9025837e+03
 -2.7603098e+03  7.9122955e+02  1.1534778e+02  6.9111353e+02
 -2.0233801e+03  4.7123022e+02  9.7488684e+02  9.0822772e+02
  1.1717987e+02  5.09822